In [17]:
from pprint import pprint


In [18]:
import numpy as np
import pandas as pd
import sqlite3
import plotly.express as px
import datetime
import time
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots



In [19]:
from pathlib import Path
database = Path().resolve() / "clubhouse_archive/Clubhouse_Dataset_v1.db"
conn = sqlite3.connect(database)
cursor = conn.cursor()


In [20]:
# all tables
cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
print(cursor.fetchall())


[('user',)]


In [21]:

df_orig = pd.read_sql("SELECT * FROM user", conn)


In [22]:
df = df_orig.drop(['twitter', 'instagram', 'photo_url'], axis=1)
# df.to_csv('clubhouse.csv')

In [23]:

df['time_created'] = pd.to_datetime(df['time_created'])

df.head(3)


user_id              name username  num_followers  num_following  \
0        4        Rohan Seth    rohan        4187268            599   
1        5      Paul Davison     paul        3718334           1861   
2        8  Johnny Appleseed   apple1             20             81   

                      time_created invited_by_user_profile  
0 2020-03-17 07:51:28.085566+00:00                    null  
1 2020-03-17 14:36:19.468976+00:00                    null  
2 2020-03-19 19:47:00.323603+00:00                    null

In [24]:
df.invited_by_user_profile.replace('null', np.nan, inplace=True)
df.invited_by_user_profile = df.invited_by_user_profile.astype('Int64')


In [25]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1300515 entries, 0 to 1300514
Data columns (total 7 columns):
 #   Column                   Non-Null Count    Dtype              
---  ------                   --------------    -----              
 0   user_id                  1300515 non-null  int64              
 1   name                     1300515 non-null  object             
 2   username                 1300515 non-null  object             
 3   num_followers            1300515 non-null  int64              
 4   num_following            1300515 non-null  int64              
 5   time_created             1300515 non-null  datetime64[ns, UTC]
 6   invited_by_user_profile  1297301 non-null  Int64              
dtypes: Int64(1), datetime64[ns, UTC](1), int64(3), object(2)
memory usage: 70.7+ MB


In [26]:
df.columns


Index(['user_id', 'name', 'username', 'num_followers', 'num_following',
       'time_created', 'invited_by_user_profile'],
      dtype='object')

### Количество зарегистрированных пользователей

In [27]:
created_times = df.sort_values('time_created')
created_times["day_created"] = created_times.time_created.dt.date
created_by_days = created_times.groupby("day_created").user_id.count()
created_cumsum_by_days = created_by_days.cumsum()
##########
uninv = created_times[created_times.invited_by_user_profile.isna()]
uninv_created_by_days = uninv.groupby("day_created").user_id.count()
uninv_created_cumsum_by_days = uninv_created_by_days.cumsum()


In [28]:
fig = go.Figure()
fig.update_layout(title_text=f"Количество новых пользователей по дням")
fig.add_trace(go.Scatter(x=created_by_days.index, y=created_by_days))
# fig.add_trace(go.Scatter(x=uninv_created_by_days.index, y=uninv_created_by_days))


**Промежуточный вывод**: 

* взровной всплеск притока пользоватлей произошел с ноября 2021 до февраля 2022

* с 10 января приток стал увеличиваться с 5 до 16 тысяч пользователей в день (к 23 января) 

In [29]:
fig = go.Figure()
fig.update_layout(
    title_text=f"Количество зарегистированных пользователей по дням")
fig.add_trace(go.Scatter(x=created_cumsum_by_days.index,
              y=created_cumsum_by_days))
# fig.add_trace(go.Scatter(x=uninv_created_cumsum_by_days.index, y=uninv_created_cumsum_by_days))


##### Задача: найти инсайты по пользователям, которые больше всех приводят новых пользователей

* Портрет пользователя, оказавшего большое влияние на рост аудитории.
* Корреляция с другими параметрами.
* Когда приходили наиболее влиятельные пользователи?


In [30]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1300515 entries, 0 to 1300514
Data columns (total 7 columns):
 #   Column                   Non-Null Count    Dtype              
---  ------                   --------------    -----              
 0   user_id                  1300515 non-null  int64              
 1   name                     1300515 non-null  object             
 2   username                 1300515 non-null  object             
 3   num_followers            1300515 non-null  int64              
 4   num_following            1300515 non-null  int64              
 5   time_created             1300515 non-null  datetime64[ns, UTC]
 6   invited_by_user_profile  1297301 non-null  Int64              
dtypes: Int64(1), datetime64[ns, UTC](1), int64(3), object(2)
memory usage: 70.7+ MB


Будем считать что влияние пользователя Х на рост аудитории - сколько Х привел друзей и сколько его друзей привели его друзья.

In [31]:
inv = df[['user_id', 'invited_by_user_profile']]
inv = inv.rename(columns={"user_id": "invited",
                 "invited_by_user_profile": "inviting"})
invited_by_none = inv[inv.inviting.isna()].invited
inv = inv[~inv.inviting.isna()].reset_index(drop=True)

In [32]:
invited_count_by_user = pd.concat([
    inv.groupby('inviting').count().invited, pd.Series(0, index=invited_by_none, name='invited')], ignore_index=True)
invited_count_by_user.describe()
mean_invited_from_1_user = invited_count_by_user.mean()

In [33]:
all_invitings = inv.copy()
all_invitings.rename(columns={'invited': '2ndgen'}, inplace=True)

all_invitings = all_invitings.merge(
    inv, how='left', left_on='2ndgen', right_on='inviting', suffixes=('_left', '_right'))
all_invitings.rename(
    columns={"inviting_left": "inviting", 'invited': "3rdgen"}, inplace=True)
all_invitings.drop('inviting_right', axis=1, inplace=True)
all_invitings = all_invitings.drop_duplicates()


In [34]:
brought_count_by_invitors = all_invitings.groupby(
    'inviting').count()['2ndgen']  # кол-во пришедших из-за inviting
brought_count_by_invitors=brought_count_by_invitors.sort_values(ascending=False)
# brought_count_by_invitors.head(30)


In [35]:
brought_count_by_invitors = pd.concat([
    brought_count_by_invitors, pd.Series(0, index=invited_by_none)], ignore_index=True)
# brought_count_by_invitors.describe()

In [36]:
px.histogram(invited_count_by_user, title='Распределение количества приведенных новых пользователей')


**Промежуточный вывод**: наиболее часто встречаемое значение == 1. 

323 тысяч пользователей привели ровно по одному другу.
96 тысяч пользователей привели ровно по 2 друга.

Какова конверсия из пригласившего одного друга в пригласившего двух друзей?

In [37]:
inv_counts = invited_count_by_user.value_counts().sort_index()
conv = (inv_counts[inv_counts.index==2].sum())/(inv_counts[inv_counts.index<=2].sum())
conv

0.2275632172510913

**Промежуточный вывод**: Пригласив одного друга, вероятность пригласить второго == 0.22

Предложение: замотивируем людей, пригласивших одного друга, пригласить второго. Поднимем конверсию до 0.42.
Получим 192 тысячи новых пользователей.

In [38]:
best_hubs = pd.Series(
    brought_count_by_invitors[brought_count_by_invitors > 50].index, name='best_hubs')
best_hubs.index = best_hubs.values
best_hubs_appearance = df.merge(best_hubs, left_on='user_id', right_index=True)[
    ['user_id', 'time_created']]
best_hubs_appearance.time_created = best_hubs_appearance.time_created.dt.date
best_hubs_counts_by_days = best_hubs_appearance.groupby('time_created').count().user_id# сгруппировать по дням, отложить на графике
# best_hubs_counts_by_days


In [39]:
fig = make_subplots(rows=2, cols=1,
                    shared_xaxes=True,
                    # vertical_spacing=0.02,
                    subplot_titles=("Новые пользователи", "Наиболее влиятельные пользователи"))

fig.add_trace(go.Scatter(x=created_by_days.index, y=created_by_days),
              row=1, col=1)


fig.add_trace(go.Histogram(x=best_hubs_appearance.time_created),
              row=2, col=1)

fig.update_layout(height=600, width=900,
                  title_text="")
fig.show()


**Промежуточный вывод**: Неожиданный факт. Несмотря на то, что пик прироста пользователей пришелся на декабрь 2020, пользователи, наиболее повлиявшие на рост аудитории, пришли в мае 2020.